# Environmental Impacts

CalCOFI was founded partly on the idea that sardine populations off the coast of California were greatly affected by environmental impacts. The region of interest, which can be seen in the following animation, is an area of great marine productivity for a variety of reasons. The California Current runs south along the coast, carrying cold waters from the Arctic region down to the equator. Additionally, off shore winds drive upwelling, the process by which warm upper ocean layers are pushed towards ocean basins and cold water from the depths rises up to replace it. This water is richer in nutrients than the warmer surface waters and is a major driver of biological productivity in the region. The following figure shows the locations of sardine larvae from 1951 to 2019, as well as the amount of larva caught during the cruises. 

In [9]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly
import plotly.express as px

In [10]:
larva = pd.read_csv('data/Fishlarvaldata_Capstone_2021_FromAndrewThompson_updated 1804 1904 1507 1607 1601 1704 1604 1501 1407 1311 ichthyoplankton by line and station.csv')
larva = larva[larva['Sardinops.sagax'] != 0.0000]
larva = larva.iloc[::-1]
larva['sardine_size'] = np.log(larva['Sardinops.sagax'])


In [11]:


fig = px.scatter_mapbox(larva, lat='latitude', lon='longitude', hover_name='Sardinops.sagax', zoom = 6, animation_frame='year', center = dict(lat=33, lon= -121), opacity = 1, size = 'sardine_size', color = 'Sardinops.sagax', color_continuous_scale= px.colors.sequential.BuPu, range_color=(0, 6100))


fig.update_layout(
    mapbox_style="white-bg",
    mapbox_layers=[
        {
            "below": 'traces',
            "sourcetype": "raster",
            "sourceattribution": "United States Geological Survey",
            "source": [
                "https://basemap.nationalmap.gov/arcgis/rest/services/USGSImageryOnly/MapServer/tile/{z}/{y}/{x}"
            ]
        }
      ])
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})


fig.show()


# Sardine's Relationship with the Ocean's Temperature

In [12]:
import numpy as np
import pandas as pd
import plotly.express as px
from sklearn.linear_model import LinearRegression
from scipy import stats
from plotly.subplots import make_subplots
import plotly.graph_objects as go

The change in ocean temperature was originally thought to be the main factor for the decline of the Pacific sardine population. Thus, we are going to explore whether the changes in our ocean's temperature had any effect on the sardine population. First, we are going to visualize ocean temperature over the years:

In [13]:
def invmercator(mercatorLat, iterations=3):
    mercatorLat = np.array(mercatorLat, dtype='float')
    approxLat = mercatorLat
    for i in range(iterations):
        approxLat = 2 * (np.arctan(np.exp(np.deg2rad(mercatorLat) +
            0.00676866 * np.sin(np.deg2rad(approxLat)))) * 180 / np.pi
            - 45)
    return(approxLat)


def tomercator(latitude):
    latitude = np.array(latitude)
    y = np.rad2deg(np.log(np.tan(np.deg2rad(45 + latitude / 2))) -
        0.00676866 * np.sin(np.deg2rad(latitude)))
    return(y)


def stationtolatlon(x, y):
    """
    x is line, y is station, or x is a matrix
    x and y are numbers, lists, tuples, or numpy arrays,
    """
    #if y == None:
        #line = x[:, 0]
        #station = x[:, 1]
    #else:
        #line = x
        #station = y
    line = x
    station = y
    line = np.array(line, dtype='float')
    station = np.array(station, dtype='float')
    
    # need reshape b/c single numbers could be wrapped in arrays
    if len(line.shape) == 0:
        line = line.reshape(1)
    
    if len(station.shape) == 0:
            station = station.reshape(1)
    
    refLatitude = 34.15 - 0.2 * (line - 80) * np.cos(np.deg2rad(30))
    latitude = refLatitude - (station - 60) * np.sin(np.deg2rad(30)) / 15
    L1 = (tomercator(latitude) - tomercator(34.15)) * np.tan(np.deg2rad(30))
    L2 = (((tomercator(refLatitude) - tomercator(latitude)) /
          (np.cos(np.deg2rad(30)) * np.sin(np.deg2rad(30)))))
    longitude = -1 * (L1 + L2 + 121.15)
    ans = np.vstack((longitude, latitude)).T
    if len(line) == 1:
        ans = ans[0]
    return(ans)


def latlontostation(x, y=None):
    """
    x and y are numbers, lists, tuples, or numpy arrays,
    x can be a matrix with y = None
    """
    #if y == None:
        #lon = x[:, 0]
        #lat = x[:, 1]
    #else:
        #lon = x
        #lat = y
    
    lon = np.array(lon, dtype='float')
    lat = np.array(lat, dtype='float')
    # need reshape b/c single numbers could be wrapped in arrays
    if len(lon.shape) == 0:
        lon = lon.reshape(1)
    if len(lat.shape) == 0:
        lat = lat.reshape(1)
    # assume we're in the western hemispere
    lon[lon > 180] = -1 * (lon[lon > 180] - 360)
    lon[lon < 0] = lon[lon < 0] * -1
    L1 = (tomercator(lat) - tomercator(34.15)) * np.tan(np.deg2rad(30))
    L2 = lon - L1 - 121.15
    mercRefLatitude = (L2 * np.cos(np.deg2rad(30)) * np.sin(np.deg2rad(30)) +
        tomercator(lat))
    refLatitude = invmercator(mercRefLatitude)
    line = 80 - (refLatitude - 34.15) * 5 / np.cos(np.deg2rad(30))
    station = 60 + (refLatitude - lat) * 15 / np.sin(np.deg2rad(30))
    ans = np.vstack((line, station)).T
    if len(line) == 1:
        ans = ans[0]
    return(ans)

In [14]:
bottle = pd.read_csv('data/sliced_bottle.csv')

In [15]:
bottle.Depth_ID.astype(str)
bottle[['year', 'month', 'day']] = bottle.Depth_ID.str.split('-', expand=True)
bottle = bottle.iloc[:,0:-2]

In [16]:
bottle = bottle.groupby(['Sta_ID', 'year']).agg({'T_degC': ['mean']})
bottle.columns = ['Avg_T_degC']
bottle = bottle.reset_index()

In [17]:
bottle.Sta_ID.astype(str)
bottle[['line', 'station']] = bottle.Sta_ID.str.split(expand=True)
bottle['line'] = bottle.line.astype(float)
bottle['station'] = bottle.station.astype(float)

line = bottle['line'].to_numpy()
station = bottle['station'].to_numpy()

In [18]:
coordinates = stationtolatlon(line, station)
lat_lon = pd.DataFrame(coordinates, columns = ['longitude', 'latitude'])
bottle = pd.concat([bottle, lat_lon], axis = 1)
bottle = bottle.sort_values(by=['year'])

In [19]:
fig = px.scatter_mapbox(bottle, lat='latitude', lon='longitude', hover_name = 'Avg_T_degC', color = 'Avg_T_degC', 
                        center=dict(lat=33, lon=-121), animation_frame='year', zoom=6)

fig.update_layout(
    mapbox_style="white-bg",
    mapbox_layers=[
        {
            "below": 'traces',
            "sourcetype": "raster",
            "sourceattribution": "United States Geological Survey",
            "source": [
                "https://basemap.nationalmap.gov/arcgis/rest/services/USGSImageryOnly/MapServer/tile/{z}/{y}/{x}"
            ]
        }
      ])
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

In [20]:
bottlecast_grouped = pd.read_csv("data/bottlecast_grouped.csv")
fig = px.line(bottlecast_grouped, x='Year', y = 'Ocean degC', title = 'Ocean Temperature Over Years')
fig.show()

Changes in climate have been affecting ocean temperatures and currents. We are going to predict that the rise in temerature near California over the years would actually BENEFIT the sardine population. A study conducted by researchers from The National Marine Fisheries Service (also known as NOAA Fisheries) found that pacific sardine tend to prefer ocean temperatures at around 11C-19C (51.8-66.2F). Using this information, I want to note a striking detail from our visualization which showcases that it was after the 1990s where ocean temperatures exceed 11 degrees celcius and reached the confort zone for the pacific sardine population. This is very similar to the time where the sardine population began to recover. Thus, let's visualize to see if the sardine population was affected by temperature in any way:

In [21]:
bottlecast_sardine = pd.read_csv('data/bottlecast_sardine.csv')
bottlecast_sardine['Count'] = bottlecast_sardine['Count'].div(4).round(0)
bottlecast_sardine = bottlecast_sardine.rename(columns={'Ocean degC':'Ocean Degrees (Celcius)'})
x_data = bottlecast_sardine['Ocean Degrees (Celcius)']
y_data = bottlecast_sardine['Count']

log_y_data = np.log(y_data)

curve_fit = np.polyfit(x_data, log_y_data, 1)

x_val = np.arange(8.5,12,.1)
y_val = np.exp(curve_fit[1]) * np.exp(curve_fit[0]*x_val)

fig = px.scatter(bottlecast_sardine, x='Ocean Degrees (Celcius)', y='Count', title = 'Ocean Temperature vs Sardine Larvae')
fig.add_traces(go.Scatter(x=x_val, y=y_val, name='Regression Fit'))
fig.show()

This model may be more realistic in that it cannot produce a negative sardine larvae value. However, visually we see that our model is imperfect and has a lot of errors. While it may not be possible to accurately predict sardine larvae amount based on ocean temperature, we can conclude that the two variables are significant enought to be related with one another in a positive correlation. 

Another factor to be considered in future models is the impact of climate cycles, such as the the El Nino Southern Oscillation (ENSO) in the Pacific Ocean. 